In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib import patches
import seaborn as sns
import folium

In [19]:
la_crime = pd.read_csv('LA_2018-PART_I_AND_II_CRIMES.csv',encoding="ISO-8859-1")

In [20]:
la_crime.head()

LURN_SAK           INCIDENT_DATE INCIDENT_REPORTED_DATE  \
0  18683229  08/29/2018 12:21:00 PM             08/30/2018   
1  18671539  08/18/2018 01:52:16 PM             08/18/2018   
2  18589376  05/24/2018 11:30:00 AM             05/24/2018   
3  18603208  06/07/2018 12:15:00 PM             06/07/2018   
4  18714901  10/02/2018 12:00:00 AM             10/02/2018   

                     CATEGORY  STAT  \
0     OFFENSES AGAINST FAMILY   175   
1             PERSONS MISSING   400   
2                    BURGLARY    64   
3  MISCELLANEOUS NON-CRIMINAL   687   
4      VEHICLE / BOATING LAWS   250   

                                           STAT_DESC  \
0  OFFENSES AGAINST FAMILY: Domestic Violence (Ot...   
1  PERSONS MISSING OR FOUND: Adult, Missing, Lost...   
2           BURGLARY, RESIDENCE: Day, Entry By Force   
3  NON-CRIMINAL, CUSTODY INCIDENTS - Inmate Sick/...   
4  VEHICLE AND BOATING LAWS: Hit And Run, Misdeme...   

                                           ADDRESS                   STREET  \
0      12100 226TH ST, HAWAIIAN GARDENS, CA  90716           12100 226TH ST   
1             2800 SANWOOD ST, LAKEWOOD, CA  90712          2800 SANWOOD ST   
2                   13500 ANKERTON ST, BASSETT, CA        13500 ANKERTON ST   
3  441 BAUCHET ST AND 3400, LOS ANGELES, CA  90012  441 BAUCHET ST AND 3400   
4         8300 GARDENDALE ST, PARAMOUNT, CA  90723       8300 GARDENDALE ST   

               CITY      ZIP     INCIDENT_ID  REPORTING_DISTRICT    SEQ  \
0  HAWAIIAN GARDENS  90716.0  018-19042-1351                1351  19042   
1          LAKEWOOD  90712.0  018-18207-1323                1323  18207   
2           BASSETT      NaN  918-06865-1463                1463   6865   
3       LOS ANGELES  90012.0  018-02451-5100                5100   2451   
4         PARAMOUNT  90723.0  918-21760-1362                1362  21760   

  GANG_RELATED    UNIT_ID           UNIT_NAME DELETED  
0           NO  CA0190013            LAKEWOOD       N  
1           NO  CA0190013            LAKEWOOD       N  
2           NO  CA0190014            INDUSTRY       N  
3           NO  CA0190058  MEN'S CENTRAL JAIL       N  
4           NO  CA0190013            LAKEWOOD       N

In [21]:
la_crime = la_crime[['ZIP','INCIDENT_ID']]
la_crime.dropna(inplace=True)

In [22]:
la_crime_total = la_crime.groupby('ZIP').count()

In [23]:
la_crime_total.reset_index(inplace=True)
la_crime_total.columns = [['ZIP','Count']]

In [24]:
la_crime_total['Count'] = la_crime_total['Count'].astype(int)
la_crime_total['ZIP'] = la_crime_total['ZIP'].astype(int)

In [25]:
la_crime_total.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 479 entries, 0 to 478
Data columns (total 2 columns):
(ZIP,)      479 non-null int32
(Count,)    479 non-null int32
dtypes: int32(2)
memory usage: 3.8 KB


In [33]:
#encoding issue, export and load back
la_crime_total.to_csv('la_crime_total.csv',index=False)

In [27]:
la_crime_total = pd.read_csv('la_crime_total.csv')

In [28]:
la_crime_total.dtypes

ZIP      int64
Count    int64
dtype: object

In [29]:
la_crime_total['logcount'] = np.log10(la_crime_total['Count'])

In [30]:
import json
# load GeoJSON
with open('Los_Angeles_City_Zip_Codes.geojson', 'r') as jsonFile:
    data = json.load(jsonFile)
tmp = data

# remove ZIP codes not in our dataset
geozips = []
for i in range(len(tmp['features'])):
    if tmp['features'][i]['properties']['ZIP'] in list(np.unique(la_crime_total.ZIP)):
        geozips.append(tmp['features'][i])

# creating new JSON object
new_json = dict.fromkeys(['type','features'])
new_json['type'] = 'FeatureCollection'
new_json['features'] = geozips

# save JSON object as updated-file
open("updated-file.json", "w").write(
    json.dumps(new_json, sort_keys=True, indent=4, separators=(',', ': '))
)

23283937

In [36]:
la = folium.Map(location=[34.05,-118.24],zoom_start=10)
la.choropleth(geo_data = r'updated-file.json', 
              data = la_crime_total, 
              columns = ['ZIP','logcount'], 
              key_on = 'feature.properties.ZIP', 
              fill_color = 'YlOrRd', fill_opacity = 0.5, line_opacity=0.5, 
              legend_name='Crime Rate in LA', reset=True)
folium.LayerControl().add_to(la)

In [37]:
la